# Out-Of-Distribution Detection (OOD) for TCR recognition 

In this notebook, we investigate the OOD problem for TCR recognition.
The in-distribution dataset is the `α+β set`+`β set` (i.e. the human data); the out-of-distribtuion dataset is the `non-human set` (mouse + macaque).

The goal of this study is to come up with a novel OOD detection method and benchmark it to a set of baseline methods.
Goal: only the human `α+β set`+`β set` (in-distribution dataset) is available at training time. We have no access to the `non-human set` (out-of-distribution dataset).

In [22]:
import pandas as pd
import torch
import numpy as np
import random
import os

from vibtcr.dataset import TCRDataset
from vibtcr.mvib.mvib import MVIB
from vibtcr.mvib.mvib_trainer import TrainerMVIB

from torch.utils.data.sampler import WeightedRandomSampler
from torch.autograd import Variable

from sklearn.model_selection import train_test_split
from tqdm import tqdm

In [23]:
from sklearn.metrics import roc_auc_score, accuracy_score, precision_score, recall_score, f1_score, precision_recall_curve, auc
import pandas as pd
import torch

metrics = [
    'auROC',
    'Accuracy',
    'Recall',
    'Precision',
    'F1 score',
    'auPRC'
]

def pr_auc(y_true, y_prob):
    precision, recall, thresholds = precision_recall_curve(y_true, y_prob)
    pr_auc = auc(recall, precision)
    return pr_auc

def get_scores(y_true, y_prob, y_pred):
    """
    Compute a df with all classification metrics and respective scores.
    """
    
    scores = [
        roc_auc_score(y_true, y_prob),
        accuracy_score(y_true, y_pred),
        recall_score(y_true, y_pred),
        precision_score(y_true, y_pred),
        f1_score(y_true, y_pred),
        pr_auc(y_true, y_prob)
    ]
    
    df = pd.DataFrame(data={'score': scores, 'metrics': metrics})
    return df

In [24]:
def set_random_seed(random_seed):
    random.seed(random_seed)
    np.random.seed(random_seed)
    torch.manual_seed(random_seed)
    torch.cuda.manual_seed(random_seed)
    torch.cuda.manual_seed_all(random_seed)

In [25]:
login = os.getlogin( )

DATA_BASE = f"/home/{login}/Git/tcr/data/"
RESULTS_BASE = f"/home/{login}/Git/tcr/notebooks/notebooks.ood/results/"

In [26]:
device = torch.device('cuda:1')
test_device = torch.device('cuda:3')

batch_size = 4096
epochs = 200
lr = 1e-3

z_dim = 150
early_stopper_patience = 20
monitor = 'auROC'
lr_scheduler_param = 10
joint_posterior = "aoe"

beta = 1e-6

# Model training

In [27]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

if os.path.isfile(RESULTS_BASE+f'avib.beta-{beta}.rep-0.pth.tar'):
    checkpoints = [
        torch.load(RESULTS_BASE+f'avib.beta-{beta}.rep-{i}.pth.tar')
        for i in range(5)
    ]
else:
    checkpoints = []

if len(checkpoints) == 0:
    for i in range(5):  # 5 independent train/test splits
        set_random_seed(i)

        df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
        df_test_out = df_out
        df_test_in = df_test_in.sample(n=len(df_test_out))
        scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler

        df_test_in['sign'] = 1  #in-distribution test set
        df_test_out['sign'] = 0  #out-of-distribution test set
        df_test = pd.concat([df_test_in, df_test_out])
        ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

        df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)

        # train loader with balanced sampling
        ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
        class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
        weight = 1. / class_count
        samples_weight = torch.tensor([weight[s] for s in df_train.sign])
        sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
        train_loader = torch.utils.data.DataLoader(
            ds_train,
            batch_size=batch_size,
            sampler=sampler
        )

        # val loader with balanced sampling
        ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
        class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
        weight = 1. / class_count
        samples_weight = torch.tensor([weight[s] for s in df_val.sign])
        sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
        val_loader = torch.utils.data.DataLoader(
            ds_val,
            batch_size=batch_size,
            sampler=sampler
        )

        model = MVIB(z_dim=z_dim, device=device, joint_posterior=joint_posterior, softmax=True).to(device)

        trainer = TrainerMVIB(
            model,
            epochs=epochs,
            lr=lr,
            beta=beta,
            checkpoint_dir=".",
            mode="bimodal",
            lr_scheduler_param=lr_scheduler_param
        )
        checkpoint = trainer.train(train_loader, val_loader, early_stopper_patience, monitor)
        trainer.save_checkpoint(checkpoint, folder='./', filename=RESULTS_BASE+f'avib.beta-{beta}.rep-{i}.pth.tar')
        checkpoints.append(checkpoint)

# Maximum Softmax Probability (MSP)
Hendrycks et al. ICLR 2017

https://arxiv.org/abs/1610.02136

In [7]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]    
    
    # test
    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    pred = model.classify(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    pred = pred.detach().numpy()
    pred = pred.max(axis=1)  # get the MSP
    df_test['prediction_'+str(i)] = pred.squeeze().tolist()

    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.msp.{joint_posterior}.rep-{i}.csv",
        index=False
    )

# Mahalanobis distance
Lee et al., NIPS 2018

https://arxiv.org/abs/1807.03888

In [8]:
# code adapted from https://github.com/pokaxpoka/deep_Mahalanobis_detector

import sklearn.covariance
from torch.autograd import Variable
from scipy.spatial.distance import pdist, cdist, squareform

def get_Mahalanobis_score(model, test_loader, num_classes, sample_mean, precision, layer_index, magnitude, mean, scale, cdr3b_only = False):
    '''
    Compute the proposed Mahalanobis confidence score on input dataset
    return: Mahalanobis score from layer_index
    '''
    model.eval()
    Mahalanobis = []
    
    for pep, cdr3b, target in test_loader:
        pep, cdr3b, target = Variable(pep, requires_grad = True), Variable(cdr3b, requires_grad = True), Variable(target)
        
        if cdr3b_only:
            if layer_index == 0:
                out_features = model.encoder_cdr3b(cdr3b)[0]  # mu
            else:
                raise NotImplementedError("if cdr3b_only, layer_index must be 0")
        else:
            if layer_index == 0:
                out_features = model(pep, cdr3b)[0]  # mu
            else:
                out_features = model(pep, cdr3b)[2]  # classification logits

        # compute Mahalanobis score
        gaussian_score = 0
        for i in range(num_classes):
            batch_sample_mean = sample_mean[layer_index][i]
            zero_f = out_features.data - batch_sample_mean
            p = precision[layer_index]
            term_gau = -0.5*torch.mm(torch.mm(zero_f, p), zero_f.t()).diag()
            if i == 0:
                gaussian_score = term_gau.view(-1,1)
            else:
                gaussian_score = torch.cat((gaussian_score, term_gau.view(-1,1)), 1)

        # Input_processing
        sample_pred = gaussian_score.max(1)[1]
        batch_sample_mean = sample_mean[layer_index].index_select(0, sample_pred)
        zero_f = out_features - Variable(batch_sample_mean)
        p = Variable(precision[layer_index])
        pure_gau = -0.5*torch.mm(torch.mm(zero_f, p), zero_f.t()).diag()
        loss = torch.mean(-pure_gau)
        loss.backward()
        
        if not cdr3b_only:
            gradient_pep =  torch.ge(pep.grad.data, 0)
            gradient_pep = (gradient_pep.float() - 0.5) * 2
            # normalizing the gradient to the same space of input
            gradient_pep = (gradient_pep.transpose(1,2) / torch.tensor(mean/scale).float()).transpose(1,2)
            tempInputs_pep = torch.add(pep.data, -magnitude, gradient_pep)
          
        gradient_cdr3b =  torch.ge(cdr3b.grad.data, 0)
        gradient_cdr3b = (gradient_cdr3b.float() - 0.5) * 2
        # normalizing the gradient to the same space of input
        gradient_cdr3b = (gradient_cdr3b.transpose(1,2) / torch.tensor(mean/scale).float()).transpose(1,2)
        tempInputs_cdr3b = torch.add(cdr3b.data, -magnitude, gradient_cdr3b)

        if cdr3b_only:
            if layer_index == 0:
                noise_out_features = model.encoder_cdr3b(Variable(tempInputs_cdr3b))[0]  # mu
            else:
                raise NotImplementedError("if cdr3b_only, layer_index must be 0")
        else:
            if layer_index == 0:
                noise_out_features = model(
                    Variable(tempInputs_pep), Variable(tempInputs_cdr3b)
                )[0]  # mu
            else:
                noise_out_features = model(
                    Variable(tempInputs_pep), Variable(tempInputs_cdr3b)
                )[2]  # classification logits

        with torch.no_grad():
            noise_out_features = noise_out_features.view(noise_out_features.size(0), noise_out_features.size(1), -1)
            noise_out_features = torch.mean(noise_out_features, 2)
            noise_gaussian_score = 0
            for i in range(num_classes):
                batch_sample_mean = sample_mean[layer_index][i]
                zero_f = noise_out_features.data - batch_sample_mean
                term_gau = -0.5*torch.mm(torch.mm(zero_f, precision[layer_index]), zero_f.t()).diag()
                if i == 0:
                    noise_gaussian_score = term_gau.view(-1,1)
                else:
                    noise_gaussian_score = torch.cat((noise_gaussian_score, term_gau.view(-1,1)), 1)      

        noise_gaussian_score, _ = torch.max(noise_gaussian_score, dim=1)
        Mahalanobis.extend(noise_gaussian_score.detach().cpu().numpy())

    return Mahalanobis


In [ ]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for experiment in range(5):  # 5 independent train/test splits
    set_random_seed(experiment)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=experiment)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=experiment)

    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )

    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    # test loader for Mahalanobis distance
    test_loader = torch.utils.data.DataLoader(
        ds_test,
        batch_size=batch_size
    )

    checkpoint = checkpoints[experiment]       

    # test
    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    model.eval()
            
    for layer_index in [0, 1]:  # 0 = mu - means of latent Gaussian; 1 = pre-softmax logits
        for magnitude in [0, 0.1, 0.01, 0.001, 0.0001]:  # different magnitude for gradient pre-processing
            
            ############# Peptide + CDR3b joint posterior #############
            sample_mean = []
            precision = []
            
            # get training samples of class 0
            pep_0 = ds_train.pep[ds_train.gt.argmax(dim=1) == torch.tensor(0)].cpu()
            cdr3b_0 = ds_train.cdr3b[ds_train.gt.argmax(dim=1) == torch.tensor(0)].cpu()
            
            # get training samples of class 1
            pep_1 = ds_train.pep[ds_train.gt.argmax(dim=1) == torch.tensor(1)].cpu()
            cdr3b_1 = ds_train.cdr3b[ds_train.gt.argmax(dim=1) == torch.tensor(1)].cpu()
            
            # pass the training samples through the trained model
            # get latent mu (mean fo the latent joint posterior) for each class
            samples_mu = [
                model(pep=pep_0, cdr3b=cdr3b_0, cdr3a=None)[0],
                model(pep=pep_1, cdr3b=cdr3b_1, cdr3a=None)[0],
            ]
            
            # pass the training samples through the trained model
            # get latent pre-softmax logits for each class
            samples_logits = [
                model(pep=pep_0, cdr3b=cdr3b_0, cdr3a=None)[2],
                model(pep=pep_1, cdr3b=cdr3b_1, cdr3a=None)[2],
            ]

            # compute mean of the mu for each class
            samples_mean_mu = torch.Tensor(2, z_dim)
            samples_mean_mu[0] = model(pep=pep_0, cdr3b=cdr3b_0, cdr3a=None)[0].mean(dim=0)
            samples_mean_mu[1] = model(pep=pep_1, cdr3b=cdr3b_1, cdr3a=None)[0].mean(dim=0)
            
            # compute mean of the pre-softmax logits for each class
            samples_mean_logits = torch.Tensor(2, 2)
            samples_mean_logits[0] = model(pep=pep_0, cdr3b=cdr3b_0, cdr3a=None)[2].mean(dim=0)
            samples_mean_logits[1] = model(pep=pep_1, cdr3b=cdr3b_1, cdr3a=None)[2].mean(dim=0)

            sample_mean.append(samples_mean_mu)
            sample_mean.append(samples_mean_logits)

            group_lasso = sklearn.covariance.EmpiricalCovariance(assume_centered=False)

            # construct inverse of covariance matrix for mu
            X = 0
            for i in range(2):
                if i == 0:
                    X = samples_mu[i] - sample_mean[0][i]
                else:
                    X = torch.cat((X, samples_mu[i] - sample_mean[0][i]), 0)

            # find inverse            
            group_lasso.fit(X.detach().cpu().numpy())
            temp_precision = group_lasso.precision_
            temp_precision = torch.from_numpy(temp_precision).float()
            precision.append(temp_precision)

            # construct inverse of covariance matrix for pre-softmax logits
            X = 0
            for i in range(2):
                if i == 0:
                    X = samples_logits[i] - sample_mean[1][i]
                else:
                    X = torch.cat((X, samples_logits[i] - sample_mean[1][i]), 0)

            # find inverse            
            group_lasso.fit(X.detach().cpu().numpy())
            temp_precision = group_lasso.precision_
            temp_precision = torch.from_numpy(temp_precision).float()
            precision.append(temp_precision)

            # compute Mahalanobis distances for all test samples (peptide+CDR3b)
            maha = get_Mahalanobis_score(model, test_loader, 2, sample_mean, precision, layer_index, magnitude, scaler.mean_, scaler.scale_, cdr3b_only=False)
            df_test['prediction_'+str(experiment)] = maha

            # save results for further analysis
            df_test.to_csv(
                RESULTS_BASE + f"non-human.mvib.{joint_posterior}.maha.layer-{layer_index}.epsilon-{magnitude}.rep-{experiment}.csv",
                index=False
            )
            
            ############# CDR3b posterior only #############
            if layer_index == 0:
                sample_mean = []
                precision = []

                # get training samples of class 0
                cdr3b_0 = ds_train.cdr3b[ds_train.gt.argmax(dim=1) == torch.tensor(0)].cpu()

                # get training samples of class 1
                cdr3b_1 = ds_train.cdr3b[ds_train.gt.argmax(dim=1) == torch.tensor(1)].cpu()

                # pass the training samples through the trained model
                # get latent mu (mean fo the latent joint posterior) for each class
                samples_mu = [
                    model.encoder_cdr3b(cdr3b_0)[0],
                    model.encoder_cdr3b(cdr3b_1)[0],
                ]

                # compute mean of the mu for each class
                samples_mean_mu = torch.Tensor(2, z_dim)
                samples_mean_mu[0] = model.encoder_cdr3b(cdr3b_0)[0].mean(dim=0)
                samples_mean_mu[1] = model.encoder_cdr3b(cdr3b_1)[0].mean(dim=0)

                sample_mean.append(samples_mean_mu)
                sample_mean.append(samples_mean_logits)

                group_lasso = sklearn.covariance.EmpiricalCovariance(assume_centered=False)

                # construct inverse of covariance matrix for mu
                X = 0
                for i in range(2):
                    if i == 0:
                        X = samples_mu[i] - sample_mean[0][i]
                    else:
                        X = torch.cat((X, samples_mu[i] - sample_mean[0][i]), 0)

                # find inverse            
                group_lasso.fit(X.detach().cpu().numpy())
                temp_precision = group_lasso.precision_
                temp_precision = torch.from_numpy(temp_precision).float()
                precision.append(temp_precision)
            
                # compute Mahalanobis distances for all test samples (CDR3b-only)
                maha = get_Mahalanobis_score(model, test_loader, 2, sample_mean, precision, layer_index, magnitude, scaler.mean_, scaler.scale_, cdr3b_only=True)
                df_test['prediction_'+str(experiment)] = maha

                # save results for further analysis
                df_test.to_csv(
                    RESULTS_BASE + f"non-human.mvib.{joint_posterior}.maha.beta-only.epsilon-{magnitude}.rep-{experiment}.csv",
                    index=False
                )

# ODIN

Liang et al., ICLR 2018
https://arxiv.org/abs/1706.02690

In [19]:
# code adapted from https://github.com/facebookresearch/odin

criterion = torch.nn.CrossEntropyLoss()

def get_odin_scores(T, magnitude, model, ds_test, mean, scale):
    pep=ds_test.pep
    cdr3b=ds_test.cdr3b
    
    _, _, pre_softmax_logits = model(pep=pep, cdr3b=cdr3b, cdr3a=None)
    
    # Calculating the confidence of the output, no perturbation added here, no temperature scaling used
    nn_outputs = pre_softmax_logits.data.cpu()
    nn_outputs = nn_outputs.numpy()
    max_val = np.max(nn_outputs, axis=1, keepdims=True)  # shape: batch size x 1 
    nn_outputs = nn_outputs - np.concatenate([max_val, max_val], axis=1)  # shape: batch size x 2
    nn_outputs = np.exp(nn_outputs)/np.sum(np.exp(nn_outputs), axis=1, keepdims=True)
    
    # Using temperature scaling
    pre_softmax_logits = pre_softmax_logits / T

    # Calculating the perturbation we need to add, that is,
    # the sign of gradient of cross entropy loss w.r.t. input
    index_max_T = torch.argmax(torch.tensor(nn_outputs), dim=1)
    labels = Variable(index_max_T)
    loss = criterion(pre_softmax_logits, labels)
    loss.backward()

    # Normalizing the gradient to binary in {0, 1}
    gradient_cdr3b =  torch.ge(cdr3b.grad.data, 0)
    gradient_cdr3b = (gradient_cdr3b.float() - 0.5) * 2
                      
    gradient_pep =  torch.ge(pep.grad.data, 0)
    gradient_pep = (gradient_pep.float() - 0.5) * 2

    # Normalizing the gradient to the same space of input tensors
    gradient_cdr3b = (gradient_cdr3b.transpose(1,2) / torch.tensor(mean/scale).float()).transpose(1,2)
    gradient_pep = (gradient_pep.transpose(1,2) / torch.tensor(mean/scale).float()).transpose(1,2)

    # Adding small perturbations to input tensors
    perturbated_cdr3b = torch.add(cdr3b.data,  -magnitude, gradient_cdr3b)
    perturbated_pep = torch.add(pep.data,  -magnitude, gradient_pep)

    outputs = model.classify(Variable(perturbated_pep), Variable(perturbated_cdr3b))
    outputs = outputs / T

    # Calculating the confidence after adding perturbations
    new_softmax = torch.softmax(outputs, dim=1)
    new_softmax = new_softmax.detach().numpy()
    
    return new_softmax

In [ ]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]     
    
    # test
    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu")).to(torch.device("cpu"))
    
    # use Variable to collect gradients of loss w.r.t. inputs
    ds_test.pep = Variable(ds_test.pep, requires_grad = True)
    ds_test.cdr3b = Variable(ds_test.cdr3b, requires_grad = True)
    
    for T in [1, 10, 100, 1000]:  # Temperature
        for magnitude in [0.1, 0.01, 0.001, 0]:  # magnitude (epsilon) for updating inputs with gradients
            ret = get_odin_scores(
                T=100, magnitude=0.1, model=model, ds_test=ds_test, mean=scaler.mean_, scale=scaler.scale_
            )
            df_test['prediction_'+str(i)] = ret.max(axis=1).tolist()

            # save results for further analysis
            df_test.to_csv(
                RESULTS_BASE + f"non-human.mvib.odin.{joint_posterior}.T-{T}.epsilon-{magnitude}.rep-{i}.csv",
                index=False
            )

# VIB
https://arxiv.org/abs/1807.00906

In [14]:
def KLD(mu, logvar):
    """Compute KL divergence between a Gaussian N(mu, logval.exp()) and a
    spherical Gaussian prior N(0, I).
    """
    KLD = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp(), dim=1)
    return KLD

In [22]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]    

    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    
    # test - joint posterior
    mu, logvar = model.infer(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    kld = -KLD(mu, logvar).detach().numpy()
    df_test['prediction_'+str(i)] = kld.tolist()

    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.kld-joint.{joint_posterior}.rep-{i}.csv",
        index=False
    )
    
    # test - CDR3b
    mu, logvar = model.encoder_cdr3b(ds_test.cdr3b)
    kld = -KLD(mu, logvar).detach().numpy()
    df_test['prediction_'+str(i)] = kld.tolist()

    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.kld-beta.{joint_posterior}.rep-{i}.csv",
        index=False
    )
    

[VAL] Best epoch 94 | Score -0.803901 | DKL-prior 0.000542 | BCE 0.667774 | auROC 0.8039:  56%|█████▋    | 113/200 [08:04<06:13,  4.29s/it]
[VAL] Best epoch 103 | Score -0.805854 | DKL-prior 0.000662 | BCE 0.679055 | auROC 0.8059:  61%|██████    | 122/200 [08:34<05:28,  4.21s/it]
[VAL] Best epoch 81 | Score -0.801426 | DKL-prior 0.000575 | BCE 0.670517 | auROC 0.8014:  50%|█████     | 100/200 [06:54<06:54,  4.14s/it]
[VAL] Best epoch 143 | Score -0.816013 | DKL-prior 0.000599 | BCE 0.750025 | auROC 0.8160:  81%|████████  | 162/200 [11:11<02:37,  4.14s/it]
[VAL] Best epoch 89 | Score -0.807759 | DKL-prior 0.000591 | BCE 0.663516 | auROC 0.8078:  54%|█████▍    | 108/200 [07:32<06:25,  4.19s/it]


# Attention + Von Neumann Entropy 

In [23]:
def get_von_neumann_entropy(rho):
    from scipy import linalg as la
    R = rho*(la.logm(rho)/la.logm(np.matrix([[2]])))
    S = -np.matrix.trace(R)
    return S

In [24]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]    
  
    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    
    # test - joint posterior
    mu, logvar = model.get_unimodal_posteriors(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    attention_mu, attention_logvar = model.experts.attention(mu, logvar)
    
    von_neumann_entropy = []
    for m in attention_logvar:
        m = m.detach().cpu().numpy()
        von_neumann_entropy.append(np.abs(get_von_neumann_entropy(m).item(0)))

    df_test['prediction_'+str(i)] = von_neumann_entropy
    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.vn-entropy.{joint_posterior}.rep-{i}.csv",
        index=False
    )


[VAL] Best epoch 140 | Score -0.806591 | DKL-prior 0.000581 | BCE 0.738173 | auROC 0.8066:  80%|███████▉  | 159/200 [11:13<02:53,  4.24s/it]


logm result may be inaccurate, approximate err = 1.8411281977954145e-07
logm result may be inaccurate, approximate err = 1.8021168163434565e-07
logm result may be inaccurate, approximate err = 9.154317875099211e-08
logm result may be inaccurate, approximate err = 4.007506203822001e-07
logm result may be inaccurate, approximate err = 5.785952213869054e-07
logm result may be inaccurate, approximate err = 2.3030796974972955e-07
logm result may be inaccurate, approximate err = 1.9379154893658764e-07
logm result may be inaccurate, approximate err = 4.5080047704248344e-07
logm result may be inaccurate, approximate err = 2.8133549416804034e-07
logm result may be inaccurate, approximate err = 2.858218278443619e-07
logm result may be inaccurate, approximate err = 1.5000634053989077e-07
logm result may be inaccurate, approximate err = 2.3176914391231285e-07
logm result may be inaccurate, approximate err = 1.9747856899782904e-07
logm result may be inaccurate, approximate err = 1.3169432587682932e

logm result may be inaccurate, approximate err = 2.3125981546741354e-07
logm result may be inaccurate, approximate err = 5.1693843145787e-07
logm result may be inaccurate, approximate err = 1.874220318416829e-07
logm result may be inaccurate, approximate err = 2.205778336081384e-07
logm result may be inaccurate, approximate err = 3.39796287288962e-07
logm result may be inaccurate, approximate err = 4.623895998522239e-07
logm result may be inaccurate, approximate err = 1.8186698596112828e-07
logm result may be inaccurate, approximate err = 1.7546333735381158e-07
logm result may be inaccurate, approximate err = 1.2852585614128822e-07
logm result may be inaccurate, approximate err = 1.697932755067464e-07
logm result may be inaccurate, approximate err = 4.781538631171005e-07
logm result may be inaccurate, approximate err = 2.3068643522243344e-07
logm result may be inaccurate, approximate err = 1.8486429833573938e-07
logm result may be inaccurate, approximate err = 2.101469934157441e-07
log

logm result may be inaccurate, approximate err = 2.8967867525898387e-07
logm result may be inaccurate, approximate err = 5.009082062494411e-07
logm result may be inaccurate, approximate err = 7.637793226556965e-08
logm result may be inaccurate, approximate err = 2.9082784456452626e-07
logm result may be inaccurate, approximate err = 3.217034757468923e-07
logm result may be inaccurate, approximate err = 2.2786382478990857e-07
logm result may be inaccurate, approximate err = 2.9399576226013943e-07
logm result may be inaccurate, approximate err = 1.2735004159575303e-07
logm result may be inaccurate, approximate err = 1.6711260892612036e-07
logm result may be inaccurate, approximate err = 2.804989685997812e-07
logm result may be inaccurate, approximate err = 3.5684183894692895e-07
logm result may be inaccurate, approximate err = 2.1701765780368529e-07
logm result may be inaccurate, approximate err = 3.938603677482656e-07
logm result may be inaccurate, approximate err = 1.7568085624215455e-

logm result may be inaccurate, approximate err = 2.7302570615052145e-07
logm result may be inaccurate, approximate err = 1.8806365821658634e-07
logm result may be inaccurate, approximate err = 1.915049959999828e-07
logm result may be inaccurate, approximate err = 5.88642524989441e-07
logm result may be inaccurate, approximate err = 2.882769853635217e-07
logm result may be inaccurate, approximate err = 1.2618060192764522e-07
logm result may be inaccurate, approximate err = 1.7178509427185858e-07
logm result may be inaccurate, approximate err = 1.597767901038458e-07
logm result may be inaccurate, approximate err = 3.1751967894836736e-07
logm result may be inaccurate, approximate err = 2.5599063319499696e-07
logm result may be inaccurate, approximate err = 2.7808700427017117e-07
logm result may be inaccurate, approximate err = 1.6323223054118733e-07
logm result may be inaccurate, approximate err = 3.154927846547479e-07
logm result may be inaccurate, approximate err = 2.687967263355583e-07

...

logm result may be inaccurate, approximate err = 4.0070198284568084e-07
logm result may be inaccurate, approximate err = 1.8168836739331918e-07
logm result may be inaccurate, approximate err = 1.8819121078234508e-07
logm result may be inaccurate, approximate err = 1.7920393272728834e-07
logm result may be inaccurate, approximate err = 3.3645342222760416e-07
logm result may be inaccurate, approximate err = 1.8875054415128848e-07
logm result may be inaccurate, approximate err = 4.094379834666065e-07
logm result may be inaccurate, approximate err = 4.57337210581184e-07
logm result may be inaccurate, approximate err = 2.377326224744697e-07
logm result may be inaccurate, approximate err = 2.7125487790173424e-07
logm result may be inaccurate, approximate err = 3.442653387715675e-07
logm result may be inaccurate, approximate err = 3.856153590193309e-07
logm result may be inaccurate, approximate err = 1.479574173157369e-07
logm result may be inaccurate, approximate err = 8.83081803832739e-08
l

logm result may be inaccurate, approximate err = 3.109042679813178e-07
logm result may be inaccurate, approximate err = 1.8396324581049325e-07
logm result may be inaccurate, approximate err = 3.7179237281158255e-07
logm result may be inaccurate, approximate err = 1.7377814358026558e-07
logm result may be inaccurate, approximate err = 6.540377307928785e-07
logm result may be inaccurate, approximate err = 4.488082716385914e-07
logm result may be inaccurate, approximate err = 4.082576049817626e-07
logm result may be inaccurate, approximate err = 9.183237885118368e-08
logm result may be inaccurate, approximate err = 1.0987024620289282e-07
logm result may be inaccurate, approximate err = 5.964183793522296e-07
logm result may be inaccurate, approximate err = 2.4376869680456626e-07
logm result may be inaccurate, approximate err = 1.63729705024763e-07
logm result may be inaccurate, approximate err = 1.836295234040715e-07
logm result may be inaccurate, approximate err = 3.4945508238399165e-07
l

logm result may be inaccurate, approximate err = 2.3753352245377318e-07
logm result may be inaccurate, approximate err = 2.311608319972154e-07
logm result may be inaccurate, approximate err = 1.1789112427632854e-07
logm result may be inaccurate, approximate err = 1.1436172183287406e-07
logm result may be inaccurate, approximate err = 4.289838881963538e-07
logm result may be inaccurate, approximate err = 1.4120560855265065e-07
logm result may be inaccurate, approximate err = 2.4460361741543144e-07
logm result may be inaccurate, approximate err = 4.2123681622559115e-07
logm result may be inaccurate, approximate err = 5.41107214020186e-07
logm result may be inaccurate, approximate err = 2.710064189719134e-07
logm result may be inaccurate, approximate err = 2.3755991478780816e-07
logm result may be inaccurate, approximate err = 3.8978998151325706e-07
logm result may be inaccurate, approximate err = 1.139080222115455e-07
logm result may be inaccurate, approximate err = 2.366213234165351e-07

logm result may be inaccurate, approximate err = 3.0538721934642873e-07
logm result may be inaccurate, approximate err = 2.577033869222294e-07
logm result may be inaccurate, approximate err = 2.429483802602267e-07
logm result may be inaccurate, approximate err = 4.4398156122176824e-07
logm result may be inaccurate, approximate err = 5.053259914766116e-07
logm result may be inaccurate, approximate err = 1.387327585855364e-07
logm result may be inaccurate, approximate err = 1.4444353698120313e-07
logm result may be inaccurate, approximate err = 2.0269987759581572e-07
logm result may be inaccurate, approximate err = 2.4945255170958787e-07
logm result may be inaccurate, approximate err = 2.30515512056531e-07
logm result may be inaccurate, approximate err = 2.92687650904911e-07
logm result may be inaccurate, approximate err = 3.998316209928069e-07
logm result may be inaccurate, approximate err = 2.414260336371319e-07
logm result may be inaccurate, approximate err = 2.972789455223424e-07
log

logm result may be inaccurate, approximate err = 1.4849167496075134e-07
logm result may be inaccurate, approximate err = 1.784170633545028e-07
logm result may be inaccurate, approximate err = 1.3944677443657771e-07
logm result may be inaccurate, approximate err = 5.148115253416534e-07
logm result may be inaccurate, approximate err = 2.206132482704466e-07
logm result may be inaccurate, approximate err = 3.9469240731655034e-07
logm result may be inaccurate, approximate err = 3.213839945261733e-07
logm result may be inaccurate, approximate err = 2.2055886657473883e-07
logm result may be inaccurate, approximate err = 1.3479327053137493e-07
logm result may be inaccurate, approximate err = 3.177711770571948e-07
logm result may be inaccurate, approximate err = 2.0459617566488832e-07
logm result may be inaccurate, approximate err = 2.6837491803289385e-07
logm result may be inaccurate, approximate err = 3.2690535430373e-07
logm result may be inaccurate, approximate err = 1.1448916418787907e-07


# Multimodal Rate

In [29]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]    

    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    
    # test - joint posterior
    mu, logvar = model.infer(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    kld_joint = -KLD(mu, logvar).detach().numpy()
    
    # test - peptide
    mu_pep, logvar_pep = model.encoder_pep(ds_test.pep)
    kld_pep = -KLD(mu_pep, logvar_pep).detach().numpy()
    
    # test - ccdr3b
    mu_cdr3b, logvar_cdr3b = model.encoder_cdr3b(ds_test.cdr3b)
    kld_cdr3b = -KLD(mu_cdr3b, logvar_cdr3b).detach().numpy()

    kld = kld_joint + kld_pep + kld_cdr3b
#     kld = np.multiply(np.multiply(kld_joint, kld_pep), kld_cdr3b)

    df_test['prediction_'+str(i)] = kld.tolist()

    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.kld-multimodal.{joint_posterior}.rep-{i}.csv",
        index=False
    )

# Attentional multimodal rate

In [16]:
df_in = pd.concat([
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/alpha-beta.csv'),
    pd.read_csv(DATA_BASE + 'alpha-beta-splits/beta.csv')
    ])

df_out = pd.read_csv(DATA_BASE + 'vdjdb/vdjdb-2021-09-05/mouse-macaco.csv')

for i in range(5):  # 5 independent train/test splits
    set_random_seed(i)

    df_train, df_test_in = train_test_split(df_in.copy(), test_size=0.2, random_state=i)
    df_test_out = df_out
    df_test_in = df_test_in.sample(n=len(df_test_out))
    scaler = TCRDataset(df_train.copy(), torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, softmax=True).scaler
    
    df_test_in['sign'] = 1  #in-distribution test set
    df_test_out['sign'] = 0  #out-of-distribution test set
    df_test = pd.concat([df_test_in, df_test_out])
    ds_test = TCRDataset(df_test, torch.device("cpu"), cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)

    df_train, df_val = train_test_split(df_train, test_size=0.2, stratify=df_train.sign, random_state=i)
        
    # train loader with balanced sampling
    ds_train = TCRDataset(df_train, device, cdr3b_col='tcrb', cdr3a_col=None, scaler=scaler, softmax=True)
    class_count = np.array([df_train[df_train.sign == 0].shape[0], df_train[df_train.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_train.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    train_loader = torch.utils.data.DataLoader(
        ds_train,
        batch_size=batch_size,
        sampler=sampler
    )
    
    # val loader with balanced sampling
    ds_val = TCRDataset(df_val, device, cdr3b_col='tcrb', cdr3a_col=None, softmax=True, scaler=scaler)
    class_count = np.array([df_val[df_val.sign == 0].shape[0], df_val[df_val.sign == 1].shape[0]])
    weight = 1. / class_count
    samples_weight = torch.tensor([weight[s] for s in df_val.sign])
    sampler = WeightedRandomSampler(samples_weight, len(samples_weight))
    val_loader = torch.utils.data.DataLoader(
        ds_val,
        batch_size=batch_size,
        sampler=sampler
    )

    checkpoint = checkpoints[i]    

    model = MVIB.from_checkpoint(checkpoint, torch.device("cpu"))
    
    # test - joint posterior
    mu, logvar = model.infer(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    kld_joint = -KLD(mu, logvar).detach().numpy()
    
    # test - peptide
    mu_pep, logvar_pep = model.encoder_pep(ds_test.pep)
    kld_pep = -KLD(mu_pep, logvar_pep).detach().numpy()
    
    # test - ccdr3b
    mu_cdr3b, logvar_cdr3b = model.encoder_cdr3b(ds_test.cdr3b)
    kld_cdr3b = -KLD(mu_cdr3b, logvar_cdr3b).detach().numpy()
    
    # attention
    mu, logvar = model.get_unimodal_posteriors(pep=ds_test.pep, cdr3b=ds_test.cdr3b, cdr3a=None)
    attention_mu, attention_logvar = model.experts.attention(mu, logvar)
    attention_mu = attention_mu.detach().numpy()
    
    kld = attention_mu[:, 0, 0] * kld_joint + attention_mu[:, 0, 1] * kld_pep + attention_mu[:, 0, 2] * kld_cdr3b

    df_test['prediction_'+str(i)] = kld.tolist()

    # save results for further analysis
    df_test.to_csv(
        RESULTS_BASE + f"non-human.mvib.kld-multimodal-attention.{joint_posterior}.rep-{i}.csv",
        index=False
    )